# Test stored procedure `pivot()`.

In [21]:
from data201 import db_connection, df_query

In [22]:
conn = db_connection(config_file = 'pivot_test.ini')
cursor = conn.cursor()

### A sample database to test `pivot`

In [23]:
cursor.execute('DROP TABLE IF EXISTS fruits')

cursor.execute(
    """
    CREATE TABLE fruits
    (
        store_id VARCHAR(8) NOT NULL,
        apples INT,
        oranges INT,
        bananas INT,
        peaches INT,
        pears INT,
        PRIMARY KEY (store_id)
    )
    """
)

In [24]:
insert_sql = (
    """
    INSERT INTO fruits
    VALUES (%(store_id)s, %(apples)s, %(oranges)s, 
            %(bananas)s, %(peaches)s, %(pears)s)
    """
)

In [25]:
fruit_data = [
    {
        'store_id': 'store_1',
        'apples':   101,
        'oranges':  102,
        'bananas':  103,
        'peaches':  104,
        'pears':    105
    },
    {
        'store_id': 'store_2',
        'apples':   201,
        'oranges':  202,
        'bananas':  203,
        'peaches':  204,
        'pears':    205
    },
    {
        'store_id': 'store_3',
        'apples':   301,
        'oranges':  302,
        'bananas':  303,
        'peaches':  304,
        'pears':    305
    }
]

In [26]:
cursor.executemany(insert_sql, fruit_data)  # NOTE: executemany()
conn.commit()

### Table `fruits` to pivot.

In [27]:
df_query(conn, 'SELECT * FROM fruits')

store_id  apples  oranges  bananas  peaches  pears
0  store_1     101      102      103      104    105
1  store_2     201      202      203      204    205
2  store_3     301      302      303      304    305

### Call stored procedure `pivot()` to pivot the table.

In [28]:
#                database: pivot_test
#              base table: fruits
#  base table primary key: store_id
# pivot table primary key: fruit_id

cursor.execute("CALL pivot('pivot_test', 'fruits', 'store_id', 'fruit_id')")

### The resulting pivoted table `fruits_pivoted`.

In [29]:
df_query(conn, 'SELECT * FROM fruits_pivoted')

fruit_id  store_1  store_2  store_3
0   apples      101      201      301
1  bananas      103      203      303
2  oranges      102      202      302
3  peaches      104      204      304
4    pears      105      205      305

In [30]:
cursor.close()
conn.close()